In [ ]:

from transformers import AutoProcessor, Idefics3ForConditionalGeneration, image_utils
import torch
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
model_id="eltorio/IDEFICS3_ROCO"
# model = AutoModelForImageTextToText.from_pretrained(model_id).to(device)
base_model_path="HuggingFaceM4/Idefics3-8B-Llama3" #or change to local path
processor = AutoProcessor.from_pretrained(base_model_path)
model = Idefics3ForConditionalGeneration.from_pretrained(
        base_model_path, torch_dtype=torch.bfloat16
    ).to(device)

model.load_adapter(model_id)

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

/opt/anaconda3/lib/python3.12/site-packages/bitsandbytes/cextension.py:34: UserWarning: The installed version of bitsandbytes was compiled without GPU support. 8-bit optimizers, 8-bit multiplication, and GPU quantization are unavailable.
  warn("The installed version of bitsandbytes was compiled without GPU support. "


'NoneType' object has no attribute 'cadam32bit_grad_fp32'


In [2]:
from transformers import image_utils
image = image_utils.load_image('https://github.com/sctg-development/ROCOv2-radiology/blob/main/source_dataset/test/ROCOv2_2023_test_000005.jpg?raw=true')

In [3]:
messages = [
    {
        "role": "user",
        "content": [
            {"type": "image"},
            {"type": "text", "text": "What do we see in this image?"},
        ]
    },
]
prompt = processor.apply_chat_template(messages, add_generation_prompt=True)
inputs = processor(text=prompt, images=[image], return_tensors="pt")
inputs = {k: v.to(device) for k, v in inputs.items()}

In [4]:
# Generate
generated_ids = model.generate(**inputs, max_new_tokens=500)
generated_texts = processor.batch_decode(generated_ids, skip_special_tokens=True)

print(generated_texts)

['User:<image>What do we see in this image?\nAssistant:  Buccal and palatal cortical bone thickness measurements.\n']
